# Using the GARCH Model

In [1]:
# Importing libraries
from arch import arch_model
import pandas as pd
import numpy as np
import itertools
import plotly.express as px
import plotly.graph_objects as go
from sklearn.preprocessing import StandardScaler
from tqdm.notebook import tqdm
from statistics import mean
from datetime import date, timedelta
import yfinance as yf

In [2]:
# Getting the date five years ago to download the current timeframe
years = (date.today() - timedelta(weeks=104)).strftime("%Y-%m-%d")

# Stocks to analyze
stocks = ['GE', 'GPRO', 'FIT', 'F']

# Getting the data for multiple stocks
df = yf.download(stocks, start=years)

print('Number of Rows: ', df.shape[0])

[*********************100%***********************]  4 of 4 completed
Number of Rows:  502


In [3]:
# Storing the dataframes in a dictionary
stock_df = {}

for col in set(df.columns.get_level_values(0)):
    
    # Assigning the information (High, Low, etc.) for each stock in the dictionary
    stock_df[col] = df[col]

# Differencing the Data
The closing prices only

In [4]:
stock_df['Diff'] = stock_df['Close'].pct_change(1).dropna() * 100

stock_df['Diff']

F       FIT         GE      GPRO
Date                                               
2018-09-21  0.407747 -2.302629  -2.327445 -0.768052
2018-09-24 -2.639596 -4.713808  -3.533280 -1.393191
2018-09-25 -2.085504  0.530039  -4.003410  3.924647
2018-09-26 -1.277954 -3.163442   1.064778  4.531725
2018-09-27 -0.431509  0.725952   1.229144  4.913297
...              ...       ...        ...       ...
2020-09-11  1.302462  0.159232  -0.833337 -1.055408
2020-09-14  1.714284  1.271859   3.361349  2.666664
2020-09-15 -1.123594  0.156989  -0.813011  1.038966
2020-09-16 -0.284091  0.940438  10.655739  3.598974
2020-09-17  3.632480 -0.077642   3.333332 -1.240699

[501 rows x 4 columns]

## Plotting the Volatility

In [5]:
for stock in stock_df['Diff'].columns:
    
    fig = px.line(stock_df['Diff'],
                  x=stock_df['Diff'].index,
                  y=stock_df['Diff'][stock],
                  title=f'Daily Return Percentage for {stock}')
    
    fig.show()

# Optimum Model Parameters

In [6]:
def param_search(model, data, order):
    """
    Loops through each iteration of the order combinations of the model and returns the best performing parameter
    with the lowest AIC score
    """
    
    # Empty list containing the combination and AIC score
    lst = []
    
    # Loop to find the best combination
    for comb in order:
        try:
            # Instantiating the model
            mod = model(data,
                        p=comb[0],
                        o=comb[1],
                        q=comb[2])
            
            # Fitting the model
            output = mod.fit()
            
            # Appending to the list
            lst.append([comb, output.aic])
        
        except:
            continue
            
    # Sorting the list
    lst = sorted(lst, key=lambda i: i[1])
    
    # Returning the combination with the lowest score
    return lst[0][0]

In [9]:
## For the param_search function
# Assigning variables to test out
p = o = q = range(0,3)

# Finding all possible combinations of p and q
poq = list(itertools.product(p, o, q))

# Testing out the Model

In [10]:
# Train test split
# 80/20 Split
split = round(stock_df['Diff'].shape[0]*.95)

train = stock_df['Diff']['F'].iloc[:split]
test = stock_df['Diff']['F'].iloc[split:]

# Optimizing parameters
best_param = param_search(arch_model, train, poq)

# Using the best parameters
model = arch_model(train, 
                   p=best_param[0],
                   o=best_param[1],
                   q=best_param[2])

output = model.fit()

# Getting the predictions
predictions = output.forecast(horizon=test.shape[0])

Iteration:      1,   Func. Count:      5,   Neg. LLF: 1759.498724990936
Iteration:      2,   Func. Count:     12,   Neg. LLF: 3654.524671138465
Iteration:      3,   Func. Count:     18,   Neg. LLF: 187065234.88499314
Iteration:      4,   Func. Count:     23,   Neg. LLF: 1127.113135026937
Iteration:      5,   Func. Count:     27,   Neg. LLF: 1126.883738301928
Iteration:      6,   Func. Count:     31,   Neg. LLF: 1126.695923433405
Iteration:      7,   Func. Count:     35,   Neg. LLF: 1126.6836714499832
Iteration:      8,   Func. Count:     39,   Neg. LLF: 1126.683072907867
Iteration:      9,   Func. Count:     43,   Neg. LLF: 1126.6830704918973
Iteration:     10,   Func. Count:     46,   Neg. LLF: 1126.683070491897
Optimization terminated successfully    (Exit mode 0)
            Current function value: 1126.6830704918973
            Iterations: 10
            Function evaluations: 46
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 2921950803.77

Iteration:      1,   Func. Count:      6,   Neg. LLF: 1336.2201872898768
Iteration:      2,   Func. Count:     13,   Neg. LLF: 1172.4411142105425
Iteration:      3,   Func. Count:     19,   Neg. LLF: 718921.8365702275
Iteration:      4,   Func. Count:     25,   Neg. LLF: 1150.4126438185567
Iteration:      5,   Func. Count:     31,   Neg. LLF: 1107.5080197326197
Iteration:      6,   Func. Count:     37,   Neg. LLF: 1095.0457174461887
Iteration:      7,   Func. Count:     42,   Neg. LLF: 1095.031521839885
Iteration:      8,   Func. Count:     47,   Neg. LLF: 1095.0311847503485
Iteration:      9,   Func. Count:     52,   Neg. LLF: 1095.0311790312633
Iteration:     10,   Func. Count:     56,   Neg. LLF: 1095.03117903128
Optimization terminated successfully    (Exit mode 0)
            Current function value: 1095.0311790312633
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      7,   Neg. LLF: 2473.76882

Iteration:      1,   Func. Count:      8,   Neg. LLF: 43516.179054083885
Iteration:      2,   Func. Count:     16,   Neg. LLF: 3376.4080852541897
Iteration:      3,   Func. Count:     25,   Neg. LLF: 1105.4885737523755
Iteration:      4,   Func. Count:     33,   Neg. LLF: 1112.4947487999175
Iteration:      5,   Func. Count:     41,   Neg. LLF: 1200.7517976336212
Iteration:      6,   Func. Count:     49,   Neg. LLF: 1068.2241856601363
Iteration:      7,   Func. Count:     56,   Neg. LLF: 1072.7944641323875
Iteration:      8,   Func. Count:     65,   Neg. LLF: 1169.13626798671
Iteration:      9,   Func. Count:     73,   Neg. LLF: 1066.473963715028
Iteration:     10,   Func. Count:     80,   Neg. LLF: 1066.4720704985657
Iteration:     11,   Func. Count:     88,   Neg. LLF: 1066.4634398735366
Iteration:     12,   Func. Count:     95,   Neg. LLF: 1066.4633206336973
Iteration:     13,   Func. Count:    102,   Neg. LLF: 1066.463315679122
Iteration:     14,   Func. Count:    109,   Neg. LLF: 1

In [11]:
garch_df = pd.DataFrame(index=test.index)

garch_df['Actual'] = test

garch_df['Predicted'] = np.sqrt(predictions.variance.values[-1,:])

px.line(garch_df, x=garch_df.index, y=['Actual', 'Predicted'])

# Using the Model

In [49]:
pred_ahead = 10

days_to_train = 100 

# Establishing new DF for predictions
stock_df['Predictions'] = pd.DataFrame(index=stock_df['Diff'].index, 
                                       columns=stock_df['Diff'].columns)

for stock in tqdm(stocks):
    
    for day in tqdm(range(250, 
                          stock_df['Diff'].shape[0]-pred_ahead, 
                          pred_ahead)):
        
        # The training data to use
        training = stock_df['Diff'][stock].iloc[day-days_to_train:day+1]
        
        # Optimizing parameters
        best_param = param_search(arch_model, training, poq)
        
        # Using the best parameters
        model = arch_model(training, 
                           p=best_param[0],
                           o=best_param[1],
                           q=best_param[2])
        
        output = model.fit()
        
        # Getting the predictions
        predictions = output.forecast(horizon=pred_ahead)
        
        # Getting the average volatility for the next N days
        stock_df['Predictions'][stock].iloc[day:day+pred_ahead] = np.sqrt(predictions.variance.values[-1,:])[-1]
        

Iteration:      1,   Func. Count:      5,   Neg. LLF: 260.0821095644304
Iteration:      2,   Func. Count:     11,   Neg. LLF: 487.1704973689177
Iteration:      3,   Func. Count:     16,   Neg. LLF: 278.2741228687738
Iteration:      4,   Func. Count:     21,   Neg. LLF: 220.9915644531477
Iteration:      5,   Func. Count:     25,   Neg. LLF: 220.92317550367432
Iteration:      6,   Func. Count:     29,   Neg. LLF: 220.9075772301443
Iteration:      7,   Func. Count:     33,   Neg. LLF: 220.88398648975905
Iteration:      8,   Func. Count:     37,   Neg. LLF: 220.8822426116445
Iteration:      9,   Func. Count:     41,   Neg. LLF: 220.88220246850048
Iteration:     10,   Func. Count:     44,   Neg. LLF: 220.88220246849525
Optimization terminated successfully    (Exit mode 0)
            Current function value: 220.88220246850048
            Iterations: 10
            Function evaluations: 44
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 20801518.911

Iteration:      1,   Func. Count:      7,   Neg. LLF: 18188196.695967663
Iteration:      2,   Func. Count:     14,   Neg. LLF: 249.85710974337073
Iteration:      3,   Func. Count:     22,   Neg. LLF: 222.8187633795292
Iteration:      4,   Func. Count:     28,   Neg. LLF: 224.80189351225653
Iteration:      5,   Func. Count:     35,   Neg. LLF: 266.06458769588806
Iteration:      6,   Func. Count:     42,   Neg. LLF: 222.48991227518542
Iteration:      7,   Func. Count:     48,   Neg. LLF: 262.59480089455167
Iteration:      8,   Func. Count:     55,   Neg. LLF: 222.42418171119922
Iteration:      9,   Func. Count:     61,   Neg. LLF: 222.42308617874724
Iteration:     10,   Func. Count:     67,   Neg. LLF: 222.4229652078844
Iteration:     11,   Func. Count:     73,   Neg. LLF: 222.42296446618442
Optimization terminated successfully    (Exit mode 0)
            Current function value: 222.42296446618442
            Iterations: 11
            Function evaluations: 73
            Gradient evalu

Iteration:      2,   Func. Count:     16,   Neg. LLF: 250.38013339168754
Iteration:      3,   Func. Count:     25,   Neg. LLF: 222.73485703415807
Iteration:      4,   Func. Count:     32,   Neg. LLF: 224.71642111966725
Iteration:      5,   Func. Count:     41,   Neg. LLF: 269.71329788750427
Iteration:      6,   Func. Count:     49,   Neg. LLF: 222.58958368873604
Iteration:      7,   Func. Count:     57,   Neg. LLF: 222.527137248431
Iteration:      8,   Func. Count:     65,   Neg. LLF: 222.42312169085716
Iteration:      9,   Func. Count:     72,   Neg. LLF: 222.42296559865838
Iteration:     10,   Func. Count:     79,   Neg. LLF: 222.4229644782386
Iteration:     11,   Func. Count:     85,   Neg. LLF: 222.4229644782598
Optimization terminated successfully    (Exit mode 0)
            Current function value: 222.4229644782386
            Iterations: 11
            Function evaluations: 85
            Gradient evaluations: 11
Iteration:      1,   Func. Count:      9,   Neg. LLF: 22425124.38

Iteration:      1,   Func. Count:      6,   Neg. LLF: 259.45526507031394
Iteration:      2,   Func. Count:     13,   Neg. LLF: 2953.108672108983
Iteration:      3,   Func. Count:     19,   Neg. LLF: 20156717.685055528
Iteration:      4,   Func. Count:     25,   Neg. LLF: 222.14840656798123
Iteration:      5,   Func. Count:     30,   Neg. LLF: 221.91100200819565
Iteration:      6,   Func. Count:     35,   Neg. LLF: 221.90406348443835
Iteration:      7,   Func. Count:     40,   Neg. LLF: 221.89864590999727
Iteration:      8,   Func. Count:     45,   Neg. LLF: 221.8888003909868
Iteration:      9,   Func. Count:     50,   Neg. LLF: 221.88676018703094
Iteration:     10,   Func. Count:     55,   Neg. LLF: 221.88660296118974
Iteration:     11,   Func. Count:     60,   Neg. LLF: 221.88659912198142
Iteration:     12,   Func. Count:     64,   Neg. LLF: 221.8865993091867
Optimization terminated successfully    (Exit mode 0)
            Current function value: 221.88659912198142
            Iterat

Iteration:      6,   Func. Count:     50,   Neg. LLF: 223.77164017877809
Iteration:      7,   Func. Count:     57,   Neg. LLF: 223.76827158161012
Iteration:      8,   Func. Count:     64,   Neg. LLF: 223.76782500331586
Iteration:      9,   Func. Count:     71,   Neg. LLF: 223.76778483527224
Iteration:     10,   Func. Count:     78,   Neg. LLF: 223.76778211296684
Iteration:     11,   Func. Count:     84,   Neg. LLF: 223.76778211308383
Optimization terminated successfully    (Exit mode 0)
            Current function value: 223.76778211296684
            Iterations: 11
            Function evaluations: 84
            Gradient evaluations: 11
Iteration:      1,   Func. Count:      9,   Neg. LLF: 20333585.573513318
Iteration:      2,   Func. Count:     18,   Neg. LLF: 242.92169805977886
Iteration:      3,   Func. Count:     29,   Neg. LLF: 230.61369701245331
Iteration:      4,   Func. Count:     39,   Neg. LLF: 226.8244915714463
Iteration:      5,   Func. Count:     48,   Neg. LLF: 223.422

...

Iteration:      9,   Func. Count:     52,   Neg. LLF: 265.4318511654946
Optimization terminated successfully    (Exit mode 0)
            Current function value: 265.4318511654946
            Iterations: 9
            Function evaluations: 52
            Gradient evaluations: 9
Iteration:      1,   Func. Count:      7,   Neg. LLF: 41426965.20800922
Iteration:      2,   Func. Count:     15,   Neg. LLF: 265.6361794785088
Iteration:      3,   Func. Count:     22,   Neg. LLF: 264.7016921947314
Iteration:      4,   Func. Count:     28,   Neg. LLF: 265.97610866779655
Iteration:      5,   Func. Count:     35,   Neg. LLF: 264.6506730984427
Iteration:      6,   Func. Count:     42,   Neg. LLF: 264.5492657422384
Iteration:      7,   Func. Count:     48,   Neg. LLF: 264.5492216671502
Iteration:      8,   Func. Count:     54,   Neg. LLF: 264.5492167794917
Iteration:      9,   Func. Count:     59,   Neg. LLF: 264.5492167792599
Optimization terminated successfully    (Exit mode 0)
            Curren

Iteration:      9,   Func. Count:     59,   Neg. LLF: 265.43185126728923
Optimization terminated successfully    (Exit mode 0)
            Current function value: 265.43185126750234
            Iterations: 9
            Function evaluations: 59
            Gradient evaluations: 9
Iteration:      1,   Func. Count:      8,   Neg. LLF: 41427503.05543688
Iteration:      2,   Func. Count:     17,   Neg. LLF: 318.83407290407564
Iteration:      3,   Func. Count:     25,   Neg. LLF: 266.9287788015633
Iteration:      4,   Func. Count:     33,   Neg. LLF: 265.48564769288856
Iteration:      5,   Func. Count:     41,   Neg. LLF: 265.54272246255834
Iteration:      6,   Func. Count:     49,   Neg. LLF: 265.2590042970674
Iteration:      7,   Func. Count:     56,   Neg. LLF: 265.61676699555323
Iteration:      8,   Func. Count:     64,   Neg. LLF: 265.2293069945334
Iteration:      9,   Func. Count:     71,   Neg. LLF: 265.2139426814913
Iteration:     10,   Func. Count:     78,   Neg. LLF: 265.090082465

Iteration:      1,   Func. Count:      6,   Neg. LLF: 320.0107953813992
Iteration:      2,   Func. Count:     13,   Neg. LLF: 282.1708127226312
Iteration:      3,   Func. Count:     20,   Neg. LLF: 274.95436175052316
Iteration:      4,   Func. Count:     26,   Neg. LLF: 265.887806557702
Iteration:      5,   Func. Count:     32,   Neg. LLF: 265.43586300171927
Iteration:      6,   Func. Count:     37,   Neg. LLF: 265.432334521318
Iteration:      7,   Func. Count:     42,   Neg. LLF: 265.4318587147583
Iteration:      8,   Func. Count:     47,   Neg. LLF: 265.43185176078504
Iteration:      9,   Func. Count:     52,   Neg. LLF: 265.4318511654946
Optimization terminated successfully    (Exit mode 0)
            Current function value: 265.4318511654946
            Iterations: 9
            Function evaluations: 52
            Gradient evaluations: 9
Iteration:      1,   Func. Count:      5,   Neg. LLF: 299.62163561030485
Iteration:      2,   Func. Count:     11,   Neg. LLF: 279.4920986261728

Iteration:      4,   Func. Count:     24,   Neg. LLF: 256.36264841398895
Iteration:      5,   Func. Count:     30,   Neg. LLF: 255.5993919392315
Iteration:      6,   Func. Count:     36,   Neg. LLF: 255.55492889433572
Iteration:      7,   Func. Count:     41,   Neg. LLF: 255.55458323140357
Iteration:      8,   Func. Count:     45,   Neg. LLF: 255.55458323147394
Optimization terminated successfully    (Exit mode 0)
            Current function value: 255.55458323140357
            Iterations: 8
            Function evaluations: 45
            Gradient evaluations: 8
Iteration:      1,   Func. Count:      7,   Neg. LLF: 2005.186286106197
Iteration:      2,   Func. Count:     16,   Neg. LLF: 260.1572072952114
Iteration:      3,   Func. Count:     23,   Neg. LLF: 258.8579843592528
Iteration:      4,   Func. Count:     30,   Neg. LLF: 261.89605376645704
Iteration:      5,   Func. Count:     37,   Neg. LLF: 255.73709819511535
Iteration:      6,   Func. Count:     44,   Neg. LLF: 255.52657111

Iteration:      1,   Func. Count:      7,   Neg. LLF: 515.5754163730776
Iteration:      2,   Func. Count:     14,   Neg. LLF: 258.137154127426
Iteration:      3,   Func. Count:     21,   Neg. LLF: 267.9872817243893
Iteration:      4,   Func. Count:     29,   Neg. LLF: 257.23080542808054
Iteration:      5,   Func. Count:     36,   Neg. LLF: 255.5605752597832
Iteration:      6,   Func. Count:     42,   Neg. LLF: 255.65364183444694
Iteration:      7,   Func. Count:     49,   Neg. LLF: 255.55482629391648
Iteration:      8,   Func. Count:     55,   Neg. LLF: 255.55445214320557
Iteration:      9,   Func. Count:     61,   Neg. LLF: 255.55444699174257
Iteration:     10,   Func. Count:     66,   Neg. LLF: 255.5544469917141
Optimization terminated successfully    (Exit mode 0)
            Current function value: 255.55444699174257
            Iterations: 10
            Function evaluations: 66
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      8,   Neg. LLF: 113937.77945

In [50]:
stock_df['Predictions'] = stock_df['Predictions'].astype(float)

# Predicted Average Values vs Actual Values

In [51]:
# Dropping the Nans
pred_df = stock_df['Predictions'].astype(float).shift(1).dropna()

# Plotting for each stock
for stock in stocks:
    
    # Plotting the volatility and comparing the results
    fig = go.Figure()
    
    fig.add_trace(go.Scatter(x=pred_df.index,
                             y=pred_df[stock],
                             name='Average Prediction',
                             mode='lines'))
    
    fig.add_trace(go.Scatter(x=pred_df.index,
                             y=stock_df['Diff'][stock].tail(len(pred_df)),
                             name='Actual',
                             mode='lines'))
    
    fig.update_layout(title=f'{pred_ahead} Day Average Volatility Comparison for {stock}',
                      xaxis_title='Date',
                      yaxis_title='% Change')
    
    fig.show()

# Trading Using Predicted Volatility

In [52]:
def position_decision(num, thres=2):
    """
    If the average forecasted volatility is low, then we buy.
    If it's is high, then we short.
    Otherwise, we don't do anything.
    """
    
    if num > thres or num < -thres:
        return -1
    
    elif num < thres and num > -thres:
        return 1
    
    else:
        return 0
    

## DF for Trading

In [61]:
trade_df = {}

# Establishing the DF for the volatility predictions 
vol_pred = stock_df['Predictions'].astype(float).dropna()

# Scaling the data in the predictions
scaler = StandardScaler()

vol_pred = pd.DataFrame(scaler.fit_transform(vol_pred), 
                        index=vol_pred.index, 
                        columns=vol_pred.columns)

# Getting positions
trade_df['Positions'] = vol_pred.applymap(lambda x: position_decision(x, thres=1) 
                                          / len(stocks))

# Preventing lookahead bias
trade_df['Positions'] = trade_df['Positions'].shift(2).dropna()
    
# Getting the log returns
trade_df['LogReturns'] = stock_df['Close'].loc[trade_df['Positions'].index].apply(np.log).diff().dropna()
    
display(vol_pred)

display(trade_df['LogReturns'])

display(trade_df['Positions'])


F       FIT        GE      GPRO
Date                                              
2019-09-20 -0.860503  2.034846 -0.664796  0.002206
2019-09-23 -0.860503  2.034846 -0.664796  0.002206
2019-09-24 -0.860503  2.034846 -0.664796  0.002206
2019-09-25 -0.860503  2.034846 -0.664796  0.002206
2019-09-26 -0.860503  2.034846 -0.664796  0.002206
...              ...       ...       ...       ...
2020-09-10 -0.175245 -0.638879 -0.720507 -1.674988
2020-09-11 -0.175245 -0.638879 -0.720507 -1.674988
2020-09-14 -0.175245 -0.638879 -0.720507 -1.674988
2020-09-15 -0.175245 -0.638879 -0.720507 -1.674988
2020-09-16 -0.175245 -0.638879 -0.720507 -1.674988

[250 rows x 4 columns]

F       FIT        GE      GPRO
Date                                              
2019-09-25  0.009831  0.007605  0.020960  0.033006
2019-09-26 -0.006543 -0.033379 -0.015402  0.012903
2019-09-27 -0.006586  0.018112  0.002215  0.071127
2019-09-30  0.008772 -0.023347 -0.011124  0.031344
2019-10-01 -0.028795 -0.015873 -0.037611  0.018156
...              ...       ...       ...       ...
2020-09-10 -0.008646 -0.011085 -0.026317 -0.053928
2020-09-11  0.012941  0.001591 -0.008368 -0.010610
2020-09-14  0.016998  0.012638  0.033061  0.026317
2020-09-15 -0.011300  0.001569 -0.008163  0.010336
2020-09-16 -0.002845  0.009360  0.101254  0.035357

[247 rows x 4 columns]

F   FIT    GE  GPRO
Date                              
2019-09-24  0.25 -0.25  0.25  0.25
2019-09-25  0.25 -0.25  0.25  0.25
2019-09-26  0.25 -0.25  0.25  0.25
2019-09-27  0.25 -0.25  0.25  0.25
2019-09-30  0.25 -0.25  0.25  0.25
...          ...   ...   ...   ...
2020-09-10  0.25  0.25  0.25 -0.25
2020-09-11  0.25  0.25  0.25 -0.25
2020-09-14  0.25  0.25  0.25 -0.25
2020-09-15  0.25  0.25  0.25 -0.25
2020-09-16  0.25  0.25  0.25 -0.25

[248 rows x 4 columns]

## Plotting the Positions

In [62]:
pos = trade_df['Positions'].apply(pd.value_counts)

# Plotting total positions
fig = px.bar(pos, 
             x=pos.index, 
             y=pos.columns,
             title='Total Positions',
             labels={'variable':'Stocks',
                      'value':'Count of Positions',
                      'index':'Position'})

fig.show()

# Calculating and Plotting Returns

## Returns for each Stock

In [63]:
# Returns
returns = trade_df['Positions'] * trade_df['LogReturns']

# Calculating the performance as we take the cumulative sum of the returns and transform the values back to normal
performance = returns.cumsum().apply(np.exp)

# Plotting the performance per stock
px.line(performance,
        x=performance.index,
        y=performance.columns,
        title='Returns Using GARCH',
        labels={'variable':'Stocks',
                'value':'Returns'})

## Returns for the Overall Portfolio vs SPY

In [64]:
# Returns for the portfolio
returns = (trade_df['Positions'] * trade_df['LogReturns']).sum(axis=1)

# Returns for SPY
spy = yf.download('SPY', start=returns.index[0])

spy = spy['Close'].apply(np.log).diff().dropna().cumsum().apply(np.exp)

# Calculating the performance as we take the cumulative sum of the returns and transform the values back to normal
performance = returns.cumsum().apply(np.exp)


# Plotting the comparison between SPY returns and GARCH returns
fig = go.Figure()

fig.add_trace(go.Scatter(x=spy.index,
                         y=spy,
                         name='SPY Returns',
                         mode='lines'))

fig.add_trace(go.Scatter(x=performance.index,
                         y=performance.values,
                         name='GARCH Returns on Portfolio',
                         mode='lines'))

fig.update_layout(title='SPY vs GARCH Overall Portfolio Returns',
                  xaxis_title='Date',
                  yaxis_title='Returns')

fig.show()

[*********************100%***********************]  1 of 1 completed
